In [7]:
# importing all the libraries
from python_speech_features import mfcc
import scipy.io.wavfile as wav


In [8]:
from glob import glob
import librosa
#importing all the libraries
import numpy as np

from tempfile import TemporaryFile
import os
import pickle
import random 
import operator

import math
import numpy as np

In [9]:
#as per the algorithm rule defining the function to get the distance between 
# feature vectors and finding the nearest neighbor
def getNeighbors(trainingSet, instance, k):
    distances = []
    for x in range (len(trainingSet)):
        dist = distance(trainingSet[x], instance, k )+ distance(instance, trainingSet[x], k)
        distances.append((trainingSet[x][2], dist))
    distances.sort(key=operator.itemgetter(1))
    neighbors = []
    for x in range(k):
        neighbors.append(distances[x][0])
    return neighbors

In [10]:
#identify the nearest neighbor
def nearestClass(neighbors):
    classVote = {}

    for x in range(len(neighbors)):
        response = neighbors[x]
        if response in classVote:
            classVote[response]+=1 
        else:
            classVote[response]=1

    sorter = sorted(classVote.items(), key = operator.itemgetter(1), reverse=True)
    return sorter[0][0]

In [11]:
#define a function for model evaluation
def getAccuracy(testSet, predictions):
    correct = 0 
    for x in range (len(testSet)):
        if testSet[x][-1]==predictions[x]:
            correct+=1
    return 1.0*correct/len(testSet)

In [12]:
directory = "genres/disco"
#for file in os.path.join(directory,file):
audio_file = glob(os.path.join(directory,"*.wav"))


In [13]:
len(audio_file)

100

In [14]:
import wave
import librosa as lr

In [15]:
#Extract features from the dataset and dump these features into a binary .dat file “my.dat”:
directory = "genres"
f= open("my.dat" ,'wb')
i=0

for folder in os.listdir(directory):
    i+=1
    if i==11 :
        break 	
    for file in os.listdir(directory+"/"+folder):	
        (rate,sig) = wav.read(directory+"/"+folder+"/"+file)
        mfcc_feat = mfcc(sig,rate,winlen=0.020, appendEnergy = False)
        covariance = np.cov(np.matrix.transpose(mfcc_feat))
        mean_matrix = mfcc_feat.mean(0)
        feature = (mean_matrix , covariance , i)
        pickle.dump(feature , f)

f.close()

In [16]:
f = open("my.dat",'rb')
f.read()

b'\x80\x03cnumpy.core.multiarray\n_reconstruct\nq\x00cnumpy\nndarray\nq\x01K\x00\x85q\x02C\x01bq\x03\x87q\x04Rq\x05(K\x01K\r\x85q\x06cnumpy\ndtype\nq\x07X\x02\x00\x00\x00f8q\x08\x89\x88\x87q\tRq\n(K\x03X\x01\x00\x00\x00<q\x0bNNNJ\xff\xff\xff\xffJ\xff\xff\xff\xffK\x00tq\x0cb\x89Ch~\xa2\x9c\xc7* S@\xa6 \'+\xf7a\xff\xbfM\xbe\x812w\x8c/\xc0\xb9\xa1\'\xf3\xbe\xa6\x0e@\xb4\xe4s\xb9W\xf2$\xc0\xc7\xb3C\xb3?\xfd\xf4?\x900\xeb\x9b\xcbd3\xc0\xd1`\x0cC\xac%\x15@.\x12?\xb5\xb8\xa10\xc0$\xe8\xc8Z\xedi\x15@\xb7\x85``\x90\xb6#\xc0+\x9eV\x16\x14\x00\x19@EmbM\x98Y\x16\xc0q\rtq\x0ebh\x00h\x01K\x00\x85q\x0fh\x03\x87q\x10Rq\x11(K\x01K\rK\r\x86q\x12h\n\x89BH\x05\x00\x00#\xd8\x97\x82D]?@\xe6e5\x06\xa2\x8c\xf5\xbf\xf3J.\xf2>X\xee\xbfbk\xd2P\xc9\x894\xc0\x8b\xd1\xfdvh+-\xc0\x90\xae\xf1z\x1b<1\xc0\xa4T"9\xf2\xb3"\xc0\xc2\xab\xd5yD\xc3\x05@\'H\xf6g\xa5R\n\xc0\xfeH\x9f?0\xa6\xf0?0\x1a$\xa3\xde\x99\x02@P\xe5\x97\xbbb]\x18@\x97rB8\x08\xe5 @\xe6e5\x06\xa2\x8c\xf5\xbf\xde9\xd8\xfe\xd1<B@G/=2\xfa\xe85\xc0~K[\x7f[\x80.

In [17]:
dataset = []
def loadDataset(filename , split , trSet , teSet):
    with open("my.dat" , 'rb') as f:
        while True:
            try:
                dataset.append(pickle.load(f))
            except EOFError:
                f.close()
                break

    for x in range(len(dataset)):
        if random.random() <split :
            trSet.append(dataset[x])
        else:
            teSet.append(dataset[x])

trainingSet = []
testSet = []
loadDataset("my.dat" , 0.80, trainingSet, testSet)

In [18]:
def distance(instance1 , instance2 , k ):
        distance = 0
        mm1 = instance1[0]
        cm1 = instance1[1]
        mm2 = instance2[0]
        cm2 = instance2[1]
        distance = np.trace(np.dot(np.linalg.inv(cm2), cm1))
        distance+=(np.dot(np.dot((mm2-mm1).transpose() , np.linalg.inv(cm2)),mm2-mm1))
        distance+= np.log(np.linalg.det(cm2)) - np.log(np.linalg.det(cm1))
        distance-= k
        return distance

In [19]:
#making prediction using KNN
leng = len(testSet)
predictions = []
for x in range (leng):
    predictions.append(nearestClass(getNeighbors(trainingSet,testSet[x] , 5))) 

accuracy1 = getAccuracy(testSet , predictions)
print(accuracy1)

0.780373831775701


In [20]:
from  collections import defaultdict
results = defaultdict(int)

i=1
for folder in os.listdir(directory):
    results[i] = folder
    i += 1
    
print(results)

defaultdict(<class 'int'>, {1: 'blues', 2: 'classical', 3: 'country', 4: 'disco', 5: 'hiphop', 6: 'jazz', 7: 'metal', 8: 'pop', 9: 'reggae', 10: 'rock'})


In [21]:
# testing the code with external samples
# URL: https://uweb.engr.arizona.edu/~429rns/audiofiles/audiofiles.html

test_dir = "test/"
test_file = test_dir + "A440Hz.wav"
#test_file = test_dir + "survesdre.wav"
# test_file = test_dir + "cutafew.wav"

In [22]:
(rate, sig) = wav.read(test_file)
mfcc_feat = mfcc(sig, rate, winlen=0.020, appendEnergy=False)
covariance = np.cov(np.matrix.transpose(mfcc_feat))
mean_matrix = mfcc_feat.mean(0)
feature = (mean_matrix, covariance, i)

In [23]:
pred = nearestClass(getNeighbors(dataset, feature, 5))
print(results[pred])

jazz
